# Skeleton Code for the Final Project

Github repo link: https://github.com/GSDSAML/prompt-engineering-2024fall/tree/main



## Leaderboard

Leaderboard updated from the Github repo.

In [1]:
import requests

url = "https://raw.githubusercontent.com/GSDSAML/prompt-engineering-2024fall/refs/heads/main/final_project/leaderboard.csv"
response = requests.get(url)

with open("leaderboard.csv", "wb") as file:
    file.write(response.content)

print("File downloaded successfully.")


File downloaded successfully.


In [2]:
import pandas as pd

# Load the leaderboard.csv file into a pandas DataFrame.
df = pd.read_csv('leaderboard.csv')

df

group_number  score  ranking   update_dt
0             0    0.2        1  2024-12-03
1            15    0.0        2  2024-12-03

## Data preparation

### You can download the FinQA train and test set here

In [3]:
!wget https://github.com/czyssrs/FinQA/raw/refs/heads/main/dataset/train.json

'wget' ���O�����Υ~���R�O�B�i���檺�{���Χ妸�ɡC


In [4]:
!wget https://github.com/czyssrs/FinQA/raw/refs/heads/main/dataset/test.json

'wget' ���O�����Υ~���R�O�B�i���檺�{���Χ妸�ɡC


## Environment Setup

In [5]:
# Install langchain
!pip install --quiet  langchain langchain-community langchainhub langchain-openai langchain-chroma bs4

In [6]:
!pip uninstall -y openai langchain langchain-openai
!pip install openai==0.27.8
!pip install langchain
!pip install langchain-openai

Found existing installation: openai 1.57.1
Uninstalling openai-1.57.1:
  Successfully uninstalled openai-1.57.1
Found existing installation: langchain 0.3.10
Uninstalling langchain-0.3.10:
  Successfully uninstalled langchain-0.3.10
Found existing installation: langchain-openai 0.2.12
Uninstalling langchain-openai-0.2.12:
  Successfully uninstalled langchain-openai-0.2.12
  Using cached openai-0.27.8-py3-none-any.whl.metadata (13 kB)
Using cached openai-0.27.8-py3-none-any.whl (73 kB)


  Using cached langchain-0.3.10-py3-none-any.whl.metadata (7.1 kB)
Using cached langchain-0.3.10-py3-none-any.whl (1.0 MB)


  Using cached langchain_openai-0.2.12-py3-none-any.whl.metadata (2.7 kB)
  Using cached openai-1.57.1-py3-none-any.whl.metadata (24 kB)
Using cached langchain_openai-0.2.12-py3-none-any.whl (50 kB)
Using cached openai-1.57.1-py3-none-any.whl (389 kB)
  Attempting uninstall: openai
    Found existing installation: openai 0.27.8
    Uninstalling openai-0.27.8:
      Successfully uninstalled openai-0.27.8


### Set API key

In [ ]:
# Set API key
OPENAI_API_KEY=""

### Prepare model

In [2]:
# Prepare model
from langchain_openai import ChatOpenAI

llm = ChatOpenAI(model="gpt-4o-mini", temperature=0.0, api_key=OPENAI_API_KEY)

## Data Preparation

### Download and unzip backup vector DB

*   Source dataset: [FinQA](https://finqasite.github.io/)
*   EDA for the FinQA dataset: https://medium.com/@sohilsharma1996/finqa-project-numerical-reasoning-over-financial-data-77a3fb4133d2

You can build your own vector DB for retrieval.

In [9]:
!wget https://github.com/GSDSAML/prompt-engineering-2024fall/raw/refs/heads/main/final_project/db.zip

'wget' ���O�����Υ~���R�O�B�i���檺�{���Χ妸�ɡC


In [10]:
!unzip db.zip

'unzip' ���O�����Υ~���R�O�B�i���檺�{���Χ妸�ɡC


### Fiscal year end date dictionary

Collected from SEC EDGAR

Dictionary with Key(ticker): Value(Fiscal year end date)

Actually, the date may different every year, but we will use this for now.

In [3]:
company_fiscal_year_end = {'GIS': '0530', 'FRT': '1231', 'MMM': '1231', 'K': '1228', 'INTC': '1228', 'CAG': '0525', 'MSI': '1231', 'FIS': '1231', 'CCI': '1231', 'CDW': '1231', 'GPN': '1231', 'TMUS': '1231', 'D': '1231', 'KMI': '1231', 'NTAP': '0426', 'TSCO': '1230', 'BLK': '1231', 'CNC': '1231', 'MRK': '1231', 'JKHY': '0630', 'VTR': '1231', 'GRMN': '1228', 'AMT': '1231', 'MAR': '1231', 'HIG': '1231', 'ADI': '1102', 'ILMN': '1229', 'NKE': '0531', 'VNO': '1231', 'FITB': '1231', 'ETR': '1231', 'KIM': '1231', 'AMAT': '1027', 'OKE': '1231', 'DG': '0131', 'TFX': '1231', 'AAL': '1231', 'EXPD': '1231', 'V': '0930', 'REGN': '1231', 'PPG': '1231', 'RCL': '1231', 'VLO': '1231', 'KHC': '1228', 'HUM': '1231', 'WELL': '1231', 'ALLE': '1231', 'UNP': '1231', 'LLY': '1231', 'TXN': '1231', 'GS': '1231', 'LKQ': '1231', 'SYY': '0629', 'IPG': '1231', 'AAP': '1228', 'ECL': '1231', 'MKTX': '1231', 'C': '1231', 'ZBH': '1231', 'UAA': '0331', 'MRO': '1231', 'AON': '1231', 'SPGI': '1231', 'ORLY': '1231', 'MO': '1231', 'PM': '1231', 'BKNG': '1231', 'BKR': '1231', 'AWK': '1231', 'APTV': '1231', 'WRK': '0930', 'SWKS': '0927', 'CMCSA': '1231', 'CE': '1231', 'CB': '1231', 'WMT': '0131', 'STT': '1231', 'RSG': '1231', 'AOS': '1231', 'AAPL': '0928', 'EXR': '1231', 'UA': '0331', 'CME': '1231', 'HII': '1231', 'HOLX': '0928', 'SLB': '1231', 'EW': '1231', 'EMR': '0930', 'VRTX': '1231', 'APD': '0930', 'ADBE': '1129', 'CAT': '1231', 'PNC': '1231', 'MAA': '1231', 'AES': '1231', 'SNA': '1228', 'JPM': '1231', 'NCLH': '1231', 'PKG': '1231', 'TROW': '1231', 'HST': '1231', 'NWS': '0630', 'MA': '1231', 'DVN': '1231', 'ANSS': '1231', 'ANET': '1231', 'SNPS': '1031', 'RL': '0328', 'DISH': '1231', 'HWM': '1231', 'FTV': '1231', 'L': '1231', 'LMT': '1231', 'MAS': '1231', 'STZ': '0228', 'EMN': '1231', 'CDNS': '1231', 'EL': '0630', 'SLG': '1231', 'BDX': '0930', 'UPS': '1231', 'MS': '1231', 'IQV': '1231', 'IP': '1231', 'EOG': '1231'}

## Define Tools

### LangChain Tool Use Example

List of pre-defined tools in LangChain: https://python.langchain.com/docs/integrations/tools/

In [4]:
from langchain_core.tools import tool


@tool
def multiply(a: int, b: int) -> int:
    """Multiply two numbers."""
    return a * b


# Let's inspect some of the attributes associated with the tool.
print(multiply.name)
print(multiply.description)
print(multiply.args)

@tool
def add(a: int, b: int) -> int:
    """Add two integers."""
    return a + b

print(add.name)
print(add.description)
print(add.args)

multiply
Multiply two numbers.
{'a': {'title': 'A', 'type': 'integer'}, 'b': {'title': 'B', 'type': 'integer'}}
add
Add two integers.
{'a': {'title': 'A', 'type': 'integer'}, 'b': {'title': 'B', 'type': 'integer'}}


In [5]:
tools = [add, multiply]

In [6]:
llm_with_tools = llm.bind_tools(tools)

query = "What is 3 * 12?"

llm_with_tools.invoke(query).tool_calls

[{'name': 'multiply',
  'args': {'a': 3, 'b': 12},
  'id': 'call_kdgBXi8WGqOqmZkmAFZORSsR',
  'type': 'tool_call'}]

In [7]:
from langchain_core.messages import HumanMessage

query = "What is 3 * 12? Also, what is 11 + 49?"

messages = [HumanMessage(query)]

ai_msg = llm_with_tools.invoke(messages)

print(ai_msg.tool_calls)

messages.append(ai_msg)

[{'name': 'multiply', 'args': {'a': 3, 'b': 12}, 'id': 'call_5WPL4MB5vzMsVPmEXRWjjp7D', 'type': 'tool_call'}, {'name': 'add', 'args': {'a': 11, 'b': 49}, 'id': 'call_Rh8SsyNyK2bEt6ucOu2TO4yo', 'type': 'tool_call'}]


In [8]:
for tool_call in ai_msg.tool_calls:
    selected_tool = {"add": add, "multiply": multiply}[tool_call["name"].lower()]
    tool_msg = selected_tool.invoke(tool_call)
    messages.append(tool_msg)

messages

[HumanMessage(content='What is 3 * 12? Also, what is 11 + 49?', additional_kwargs={}, response_metadata={}),
 AIMessage(content='', additional_kwargs={'tool_calls': [{'id': 'call_5WPL4MB5vzMsVPmEXRWjjp7D', 'function': {'arguments': '{"a": 3, "b": 12}', 'name': 'multiply'}, 'type': 'function'}, {'id': 'call_Rh8SsyNyK2bEt6ucOu2TO4yo', 'function': {'arguments': '{"a": 11, "b": 49}', 'name': 'add'}, 'type': 'function'}], 'refusal': None}, response_metadata={'token_usage': {'completion_tokens': 50, 'prompt_tokens': 83, 'total_tokens': 133, 'completion_tokens_details': {'accepted_prediction_tokens': 0, 'audio_tokens': 0, 'reasoning_tokens': 0, 'rejected_prediction_tokens': 0}, 'prompt_tokens_details': {'audio_tokens': 0, 'cached_tokens': 0}}, 'model_name': 'gpt-4o-mini-2024-07-18', 'system_fingerprint': 'fp_bba3c8e70b', 'finish_reason': 'tool_calls', 'logprobs': None}, id='run-a86920b2-d7a3-42c9-a9c7-2e55aa440c50-0', tool_calls=[{'name': 'multiply', 'args': {'a': 3, 'b': 12}, 'id': 'call_5WP

In [9]:
llm_with_tools.invoke(messages).content

'The result of \\(3 \\times 12\\) is 36, and the result of \\(11 + 49\\) is 60.'

### Extract fiscal tool

In [10]:
company_fiscal_year_end

{'GIS': '0530',
 'FRT': '1231',
 'MMM': '1231',
 'K': '1228',
 'INTC': '1228',
 'CAG': '0525',
 'MSI': '1231',
 'FIS': '1231',
 'CCI': '1231',
 'CDW': '1231',
 'GPN': '1231',
 'TMUS': '1231',
 'D': '1231',
 'KMI': '1231',
 'NTAP': '0426',
 'TSCO': '1230',
 'BLK': '1231',
 'CNC': '1231',
 'MRK': '1231',
 'JKHY': '0630',
 'VTR': '1231',
 'GRMN': '1228',
 'AMT': '1231',
 'MAR': '1231',
 'HIG': '1231',
 'ADI': '1102',
 'ILMN': '1229',
 'NKE': '0531',
 'VNO': '1231',
 'FITB': '1231',
 'ETR': '1231',
 'KIM': '1231',
 'AMAT': '1027',
 'OKE': '1231',
 'DG': '0131',
 'TFX': '1231',
 'AAL': '1231',
 'EXPD': '1231',
 'V': '0930',
 'REGN': '1231',
 'PPG': '1231',
 'RCL': '1231',
 'VLO': '1231',
 'KHC': '1228',
 'HUM': '1231',
 'WELL': '1231',
 'ALLE': '1231',
 'UNP': '1231',
 'LLY': '1231',
 'TXN': '1231',
 'GS': '1231',
 'LKQ': '1231',
 'SYY': '0629',
 'IPG': '1231',
 'AAP': '1228',
 'ECL': '1231',
 'MKTX': '1231',
 'C': '1231',
 'ZBH': '1231',
 'UAA': '0331',
 'MRO': '1231',
 'AON': '1231',
 'SP

Extract company ticker from the question

We used LLM for now, but may need to connect DB for stability.

In [11]:
from langchain_core.prompts import PromptTemplate

extract_ticker_prompt = PromptTemplate(
    input_variables=["question"],
    template="""
    You have to extract the company name in the given question, and answer the ticker of the company.
    Answer in JSON format, with 'ticker' key.

    Question: {question}

    Output JSON: {{
      "ticker": "<ticker of the company>"
    }}
    """
)

from pydantic import BaseModel, Field

class Ticker(BaseModel):
    """Ticker of the company in the given question"""
    ticker: str = Field(description="ticker of the company")

extract_ticker_chain = extract_ticker_prompt | llm.with_structured_output(Ticker)

In [13]:
extract_ticker_chain.invoke({"question": "What was the revenue of Apple in 2022?"})

Ticker(ticker='AAPL')

In [14]:
from langchain_core.output_parsers import StrOutputParser
from datetime import datetime

parser = StrOutputParser()

change_prompt = PromptTemplate(
    input_variables=["original_question", "fiscal_info", "today"],
    template="""
    You have to convert relative time information in the given original question to the fiscal year of the company.
    Use the fiscal end date to convert to fiscal year.
    Answer only the converted question.

    Original question: {original_question}
    Fiscal end date for the company: {fiscal_info}
    Today date: {today}
    """
)

convert_chain = change_prompt | llm | parser

def get_fiscal_info_with_ticker(ticker: str) -> str:
    """Get fiscal year information of the company with ticker string."""
    ticker = ticker.upper()
    if ticker in company_fiscal_year_end:
      end_date = company_fiscal_year_end[ticker]
      return end_date[:2] + '-' + end_date[2:]
    else:
      return '12-31'

extract_fiscal_prompt = PromptTemplate(
    input_variables=["question"],
    template="""
    You have to extract the fiscal year in the given question.
    Answer in JSON format, with 'fy' key.

    Question: {question}

    Output JSON: {{
      "fy": <fiscal year in the question>
    }}
    """
)

from pydantic import BaseModel, Field

class FiscalYear(BaseModel):
    """FiscalYear mentioned in the given question"""
    fy: int = Field(description="fiscal year in the question")

extract_fiscal_chain = extract_fiscal_prompt | llm.with_structured_output(FiscalYear)

In [15]:
from langchain_core.tools import tool

@tool
def rewrite2fiscal(question: str) -> tuple[str, int]:
  """Extract the company and convert relative time information in the question to the actual fiscal year of the company.
     It uses today function for the date information.

    Args:
        question: Question to be extracted.

    Returns:
        A tuple of ticker of the company and the fiscal year
  """
  ticker = extract_ticker_chain.invoke({"question": question}).ticker
  today = datetime.now().strftime("%Y-%m-%d")
  response = convert_chain.invoke({"original_question": question, "fiscal_info": get_fiscal_info_with_ticker(ticker), "today": today})
  fy = extract_fiscal_chain.invoke({'question': response}).fy
  return ticker, fy

In [16]:
rewrite2fiscal("What was the revenue of Apple in 2023-07-10?")

C:\Users\mindy\AppData\Local\Temp\ipykernel_13600\2947161642.py:1: LangChainDeprecationWarning: The method `BaseTool.__call__` was deprecated in langchain-core 0.1.47 and will be removed in 1.0. Use :meth:`~invoke` instead.
  rewrite2fiscal("What was the revenue of Apple in 2023-07-10?")


('AAPL', 2023)

In [17]:
rewrite2fiscal("What was the revenue of Apple in 2023-12-20?")

('AAPL', 2024)

In [18]:
rewrite2fiscal("What was the revenue of Apple in last year?")

('AAPL', 2023)

In [19]:
rewrite2fiscal("What was the revenue of Apple in this year?")

('AAPL', 2024)

### Domain specific calulation tools

You should implement more tools to answer complex questions.

In [20]:
@tool
def calculate_eps(net_income: float, outstanding_shares: int):
  """Calculate the EPS of the company using net income and outstanding share

   Args:
        net_income: Net income value of the company
        outstanding_shares: Total stock held by the company's shareholders

    Returns:
        EPS value
  """
  if (net_income is None) or (outstanding_shares is None):
    print("Give me the net income and outstanding shares first")
    return None
  elif outstanding_shares == 0:
    print("Outstanding shares cannot be zero")
    return None

  return net_income / outstanding_shares

In [21]:
@tool
def calculate_cashflowfromoperations(net_income: float, non_cash_items: float, changes_in_working_capital: float):
  """Calculate the cash flow from operations of the company using net income, non cash items and change in working capital

   Args:
        net_income: Net income value of the company
        non_cash_items: Financial transactions or events that are recorded in a company's financial statements but do not involve the exchange of cash
        changes_in_working_capital: Difference in a company's working capital between two reporting periods

    Returns:
        Value of cash flow from operations
  """
  if (net_income is None) or (non_cash_items is None) or (changes_in_working_capital is None):
    print("Give me the net income, non cash items and change in working capital data first")
    return None

  return net_income + non_cash_items + changes_in_working_capital

### Retriever Tool

#### Build Vector DB

You can skip this part for demo.

In [23]:
import json

def load_and_view_sample(file_path):
  """Loads a JSON file and prints a sample of its contents."""
  try:
    with open(file_path, 'r') as f:
      data = json.load(f)
      print("Sample Data from JSON:")
      print(json.dumps(data, indent=2)[:500]) # Print first 500 chars for sample
  except FileNotFoundError:
    print(f"File not found: {file_path}")
  except json.JSONDecodeError:
    print(f"Error decoding JSON from file: {file_path}")


# Assuming your file is named 'test.json' in the current directory
load_and_view_sample('test.json')

Sample Data from JSON:
[
  {
    "pre_text": [
      "entergy corporation and subsidiaries management 2019s financial discussion and analysis a result of the entergy louisiana and entergy gulf states louisiana business combination , results of operations for 2015 also include two items that occurred in october 2015 : 1 ) a deferred tax asset and resulting net increase in tax basis of approximately $ 334 million and 2 ) a regulatory liability of $ 107 million ( $ 66 million net-of-tax ) as a result of customer credits 


In [24]:
import json

def count_rows_in_json(file_path):
  """Counts the number of rows (objects) in a JSON file."""
  try:
    with open(file_path, 'r') as f:
      data = json.load(f)
      if isinstance(data, list):
        return len(data)
      elif isinstance(data, dict):
        return len(data)
      else:
        return 0  # Or raise an error, depending on your needs
  except FileNotFoundError:
    print(f"File not found: {file_path}")
    return 0
  except json.JSONDecodeError:
    print(f"Error decoding JSON from file: {file_path}")
    return 0

# Assuming your file is named 'test.json' in the current directory
num_rows = count_rows_in_json('test.json')
print(f"Number of rows in the JSON file: {num_rows}")

Number of rows in the JSON file: 1147


In [25]:
import json

def analyze_json(file_path):
  """Analyzes a JSON file, printing information about its attributes."""
  try:
    with open(file_path, 'r') as f:
      data = json.load(f)
      if isinstance(data, list):
        print("JSON file contains a list of objects.")
        if len(data) > 0:
          print("Example object:")
          print(json.dumps(data[0], indent=2))
          for key in data[0].keys():
            print(f"- Attribute: {key}")
      elif isinstance(data, dict):
        print("JSON file contains a dictionary.")
        print("Attributes:")
        for key in data.keys():
          print(f"- Attribute: {key}")
      else:
        print("JSON file is empty or contains an unexpected data type.")
  except FileNotFoundError:
    print(f"File not found: {file_path}")
  except json.JSONDecodeError:
    print(f"Error decoding JSON from file: {file_path}")

# Analyze 'test.json'
analyze_json('test.json')

JSON file contains a list of objects.
Example object:
{
  "pre_text": [
    "entergy corporation and subsidiaries management 2019s financial discussion and analysis a result of the entergy louisiana and entergy gulf states louisiana business combination , results of operations for 2015 also include two items that occurred in october 2015 : 1 ) a deferred tax asset and resulting net increase in tax basis of approximately $ 334 million and 2 ) a regulatory liability of $ 107 million ( $ 66 million net-of-tax ) as a result of customer credits to be realized by electric customers of entergy louisiana , consistent with the terms of the stipulated settlement in the business combination proceeding .",
    "see note 2 to the financial statements for further discussion of the business combination and customer credits .",
    "results of operations for 2015 also include the sale in december 2015 of the 583 mw rhode island state energy center for a realized gain of $ 154 million ( $ 100 million n

In [26]:
from langchain_openai import ChatOpenAI
from langchain_core.tools import tool
from langchain_core.messages import HumanMessage
from langchain_core.prompts import PromptTemplate
from pydantic import BaseModel, Field
from langchain_core.output_parsers import StrOutputParser
from datetime import datetime
import json

# Define pre_text and post_text
pre_text = """
## Financial Data Analysis with Tools

This system is designed to analyze financial data and answer your questions about companies.
It uses tools like calculating metrics (EPS, cash flow from operations) and retrieving information from a financial dataset.

"""

post_text = """
**Note:** The system may not always have the information you're looking for.
If the response is insufficient, please refine your question or provide more details.
"""

# Define a table with examples
table = """
| Question Example | Expected Outcome |
|---|---|
| What was Apple's EPS in 2022? | Retrieves Apple's 2022 net income and shares outstanding, then calculates and returns EPS. |
| What was the cash flow from operations for Microsoft in 2023? | Retrieves Microsoft's net income, non-cash items, and changes in working capital, then calculates and returns cash flow from operations. |
"""

# Combine pre_text, post_text, and table
combined_text = f"{pre_text}\n\n**Example Usage:**\n\n{table}\n\n{post_text}"

# Function to ask ChatGPT and compare answers
def qa_and_compare(question):
    prompt_with_context = f"{combined_text}\n\n**Question:** {question}"

    messages = [HumanMessage(content=prompt_with_context)]

    ai_msg = llm.invoke(messages)

    print("ChatGPT's Answer:")
    print(ai_msg.content)


# Example question
question = "What was the revenue of Apple in 2022?"

qa_and_compare(question)

ChatGPT's Answer:
To provide you with the revenue of Apple in 2022, I would need to retrieve the relevant financial data. However, I currently do not have access to real-time financial datasets. 

As of my last update, Apple's revenue for the fiscal year 2022 was approximately $394.3 billion. For the most accurate and up-to-date information, please refer to Apple's official financial statements or a reliable financial news source.


In [27]:
with open('train.json', 'r') as f:
    train_data = json.load(f)

# Generate distinct_items_with_context
distinct_items_with_context = {}

for item in train_data:
    filename = item['filename']

    distinct_items_with_context[filename] = {
        'pre_text': item.get('pre_text', []),
        'post_text': item.get('post_text', []),
        'table': item.get('table', [])
    }

#Check the generated dictionary
print(f"Generated distinct_items_with_context with {len(distinct_items_with_context)} items.")

def merge_text_list(text_list):
    """Merge a list of strings into a single string with newline separation."""
    if not isinstance(text_list, list):
        raise ValueError("Input must be a list of strings.")
    return "\n".join(text_list)

Generated distinct_items_with_context with 2110 items.


In [28]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.vectorstores import Chroma

# Initialize the text splitter and embeddings
splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=50)
embeddings = OpenAIEmbeddings(model='text-embedding-3-small', api_key=OPENAI_API_KEY)

# Assuming 'distinct_items_with_context' is a dictionary as shown in your code
for filename, context_data in distinct_items_with_context.items():
    # Merge pre_text and post_text
    pre_text = merge_text_list(context_data['pre_text'])
    post_text = merge_text_list(context_data['post_text'])
    table = "\n".join([" | ".join(row) for row in context_data['table']])  # Convert table to string

    # Split the pre-text and post-text into smaller chunks
    pre_text_chunks = splitter.split_text(pre_text)
    post_text_chunks = splitter.split_text(post_text)

    # Create a list of texts to store in the vector DB
    texts_for_db = []
    metadatas_for_db = []

    # Add pre-text chunks
    for chunk in pre_text_chunks:
        if isinstance(chunk, str):  # Ensure the chunk is a string
            texts_for_db.append(chunk)
            metadatas_for_db.append({'filename': filename, 'context_type': 'pre_text'})

    # Add table
    if isinstance(table, str) and table.strip():  # Ensure the table is a non-empty string
        texts_for_db.append(table)
        metadatas_for_db.append({'filename': filename, 'context_type': 'table'})

    # Add post-text chunks
    for chunk in post_text_chunks:
        if isinstance(chunk, str):  # Ensure the chunk is a string
            texts_for_db.append(chunk)
            metadatas_for_db.append({'filename': filename, 'context_type': 'post_text'})

    # Debugging: Print the texts to ensure they are all strings
    print("Texts for DB:", texts_for_db)

    # Create the vector database for each file
    docsearch = Chroma.from_texts(
        texts_for_db,
        embeddings,
        metadatas=metadatas_for_db,
        persist_directory="./db_train 500_50"
    )

# Save the vector database
docsearch.persist()

C:\Users\mindy\AppData\Local\Temp\ipykernel_13600\2828497550.py:7: LangChainDeprecationWarning: The class `OpenAIEmbeddings` was deprecated in LangChain 0.0.9 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-openai package and should be used instead. To use it run `pip install -U :class:`~langchain-openai` and import as `from :class:`~langchain_openai import OpenAIEmbeddings``.
  embeddings = OpenAIEmbeddings(model='text-embedding-3-small', api_key=OPENAI_API_KEY)


Texts for DB: ['interest rate to a variable interest rate based on the three-month libor plus 2.05% ( 2.05 % ) ( 2.34% ( 2.34 % ) as of october 31 , 2009 ) .\nif libor changes by 100 basis points , our annual interest expense would change by $ 3.8 million .\nforeign currency exposure as more fully described in note 2i .\nin the notes to consolidated financial statements contained in item 8 of this annual report on form 10-k , we regularly hedge our non-u.s .', 'dollar-based exposures by entering into forward foreign currency exchange contracts .\nthe terms of these contracts are for periods matching the duration of the underlying exposure and generally range from one month to twelve months .\ncurrently , our largest foreign currency exposure is the euro , primarily because our european operations have the highest proportion of our local currency denominated expenses .', 'relative to foreign currency exposures existing at october 31 , 2009 and november 1 , 2008 , a 10% ( 10 % ) unfavora

C:\Users\mindy\AppData\Local\Temp\ipykernel_13600\2828497550.py:53: LangChainDeprecationWarning: Since Chroma 0.4.x the manual persistence method is no longer supported as docs are automatically persisted.
  docsearch.persist()


In [ ]:
#!zip -r ./db.zip ./db

In [29]:
query = "What was the revenue of Apple in 2012?"
docs = docsearch.similarity_search(query)

for doc in docs:
  print(doc.page_content)
  print(doc.metadata)
  print('--------------')

( in millions ) | 2013 | 2012 | 2011
net revenue | $ 33039 | $ 34504 | $ 35624
operating income | $ 11827 | $ 13106 | $ 14840
{'context_type': 'table', 'filename': 'INTC/2013/page_40.pdf'}
--------------
in millions | 2012 | 2011 | 2010
sales | $ 13280 | $ 10430 | $ 9840
operating profit | 1066 | 1147 | 826
{'context_type': 'table', 'filename': 'IP/2012/page_55.pdf'}
--------------
net sales for 2013 increased 12% ( 12 % ) to $ 14.8 billion compared with $ 13.3 billion in 2012 , and 42% ( 42 % ) compared with $ 10.4 billion in 2011 .
operating profits were 69% ( 69 % ) higher in 2013 than in 2012 and 57% ( 57 % ) higher than in 2011 .
{'context_type': 'pre_text', 'filename': 'IP/2013/page_61.pdf'}
--------------
 | december 31 2013 ( in millions )
revenue | $ 40782
net income | 2707
{'context_type': 'table', 'filename': 'AAL/2015/page_187.pdf'}
--------------


#### Load Vector DB

In [55]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.vectorstores import Chroma

embeddings = OpenAIEmbeddings(model='text-embedding-3-small',api_key=OPENAI_API_KEY)

from langchain_chroma import Chroma

docsearch = Chroma(
    persist_directory="./db",
    embedding_function=embeddings
)

#### Retriever tool with filtered search

In [58]:
def retrieve(question:str, ticker: str, fy: int) -> list[str]:
  """Search vector DB for the financial reports with the question and ticker and fiscal year

   Args:
        question: Question need to be answered
        ticker: Ticker of the company for filtering the documents
        fy: Fiscal year for filtering the documents

    Returns:
        A related document for the question.
  """
  retriever = docsearch.as_retriever(search_kwargs={'k': 1, 'filter':
  {
      "$and": [
          {
              "company": {
                  "$eq": ticker
              }
          },
          {
              "fiscal": {
                  "$eq": fy
              }
          }
      ]
  }})

#   retriever = docsearch.as_retriever(search_kwargs={"k": 1})
  result = retriever.invoke(question)
#   print("Result without filters:", result)


  result = retriever.invoke(question)
  if result:
    return result
  else:
    return ["No data returned. Try again with correct ticker and fiscal year, or different question"]

In [59]:
retrieve("what was the hqla in the q4 of Citigroup in 2015?","AAPL", 2012)

[Document(metadata={'company': 'AAPL', 'context_type': 'post_text', 'fiscal': 2012}, page_content='conjunction with this dividend on august 16 , 2012 .no dividends were declared in the first three quarters of 2012 or in 2011 and 2010. .')]

In [34]:
@tool
def retrieve_factual_data(question:str, ticker: str, fy: int) -> str:
  """Search vector DB for the financial reports with the question and ticker and fiscal year

   Args:
        question: Question need to be answered
        ticker: Ticker of the company for filtering the documents
        fy: Fiscal year for filtering the documents

    Returns:
        A related document for the question.
  """
  retriever = docsearch.as_retriever(search_kwargs={'k': 1, 'filter':
  {
      "$and": [
          {
              "company": {
                  "$eq": ticker
              }
          },
          {
              "fiscal": {
                  "$eq": fy
              }
          }
      ]
  }})
  result = retriever.invoke(question)
  if result:
    return result[0].page_content
  else:
    return "No data returned. Try again with correct ticker and fiscal year, or different question"

## Agent with tools

In [61]:
from langchain_core.messages import HumanMessage, SystemMessage
from langchain_core.prompts import ChatPromptTemplate

def agentic_rag(query: str) -> str:
  tools = [rewrite2fiscal, calculate_eps, calculate_cashflowfromoperations, retrieve_factual_data]
  system_query = (
    "You are a professional financial assistant capable of answering complex financial questions using the following tools: "
    "rewrite2fiscal, calculate_eps, calculate_cashflowfromoperations, and retrieve_factual_data. "
    "If the answer is clear from the chat history or your internal knowledge, provide it directly. "
    "If tools are needed, select the most relevant tool and specify its arguments to retrieve or compute the answer. "
    "Always aim for accuracy and clarity in your responses.")

  user_query = (
    "You are tasked with answering the following financial question. If you can answer directly based on the given "
    "information, do so. If not, decide which tool to use and specify the arguments required to get the answer.\n\n"
    "Question: {question}")

  messages = [SystemMessage(content=system_query), HumanMessage(content=user_query.format(question=query))]
  llm_with_tools = llm.bind_tools(tools)
  ai_msg = llm_with_tools.invoke(messages)
  # print(ai_msg.content)
  while ai_msg.content == '':
    messages.append(ai_msg)
    for tool_call in ai_msg.tool_calls:
      selected_tool = {"rewrite2fiscal": rewrite2fiscal,
                      "calculate_eps": calculate_eps,
                      "calculate_cashflowfromoperations": calculate_cashflowfromoperations,
                      "retrieve_factual_data": retrieve_factual_data}[tool_call["name"].lower()]
      tool_msg = selected_tool.invoke(tool_call)
      messages.append(tool_msg)
    ai_msg = llm_with_tools.invoke(messages)
    # print(ai_msg.content)

  # for message in messages:
  #   print(message)
  return ai_msg.content

In [62]:
response = agentic_rag("what was brazilian paper sales of International Paper Company in 2006?")

In [63]:
response

"The retrieved information does not provide specific figures for Brazilian paper sales of International Paper Company in 2006. It mentions that significant steps were taken in 2006, including the sale of their Brazilian coated papers business, but does not specify the sales figures.\n\nUnfortunately, I cannot provide the exact sales figures for that year based on the available data. You may need to consult the company's financial reports or other detailed financial databases for precise information on Brazilian paper sales in 2006."

## Scoring section

Use this Q&A dictionary to test your project code.

You should not change the scoring prompt.

You can submit your accuracy result with the screenshot to TA email, then I will post the score to the leaderboard.

In [41]:
qa_dict = [{'Question': '"what was the hqla in the q4 of Citigroup in 2015"',
  'Answer': '"378.5 billion dollars"'},
 {'Question': '"as a result of the sales of certain non-core towers and other assets what was the recorded net losses of American Tower in 2008"',
  'Answer': '"10.5 million dollars"'},
 {'Question': '"what was the port call costsin of Royal Caribbean Cruises in 2012"',
  'Answer': '"459.8 million dollars"'},
 {'Question': '"what is the aggregate rent expense of American Tower Corp in 2014?"',
  'Answer': '"655.0 million dollars"'},
 {'Question': '"what is the long-term component of BlackRock at 12/31/2011?"',
  'Answer': '"593356 million dollars"'},
 {'Question': '"at december 31 , 2012 of The PNC Financial Services, what was the potential maximum exposure under the loss share arrangements?"',
  'Answer': '"3.9 billion dollars"'},
 {'Question': '"what is the total financial liabilities at fair value of Goldman Sachs in 2012?"',
  'Answer': '"377677 million dollars"'},
 {'Question': '"what was brazilian paper sales of International Paper Company in 2006?"',
  'Answer': '"6930 million dollars"'},
 {'Question': '"what was brazilian paper sales of International Paper Company in 2005?"',
  'Answer': '"7170 million dollars"'},
 {'Question': '"what is the cashflow of Kellogg in 2006?"',
  'Answer': '"957.4 million dollars"'},
 {'Question': '"From the perspective of 5 years ago, what percentage of total minimum lease payments of Dish Network are due in 2015?"',
  'Answer': '"10%"'},
 {'Question': '"in 2011 what was the SL Green Realty Corp\'s percent of the change in the account balance at end of year"',
  'Answer': '"93.7%"'},
 {'Question': '"what was the value in thousands of unvested restricted stock and performance awards at the weighted-averagegrant-datefair value as of december 31 , 2018 of Global Payments?"',
  'Answer': '"117624.84"'},
 {'Question': '"based on the cash dividends paid of the year, how many common stock shares were outstanding in 2007 Snap-on?"',
  'Answer': '"58909091"'},
 {'Question': '"what is the Entergy Corp\'s 2008 total value , in millions of dollars , of issuable long-term securities?"',
  'Answer': '"1450"'},
 {'Question': '"for the capital framework of Goldman Sachs Group 7 years ago, what percent of the minimum supplementary leverage ratio consisted of a buffer?"',
  'Answer': '"40%"'},
 {'Question': '"in 2007 what was the 3M\'s ratio of the interest expense to the interest income"',
  'Answer': '"1.59"'},
 {'Question': '"what is the AON\'s decrease observed in the additions for tax positions of prior years as of 2018, in millions?"',
  'Answer': '"2"'},
 {'Question': '"In 2014 Global Payments, what is the total value of securities approved by security holders but net yer issued , ( in millions ) ?"',
  'Answer': '"365.4"'},
 {'Question': '"what is the percent of our network route miles that is owned rather than operated on pursuant to trackage rights or leases in 2016 Union Pacific Corp"',
  'Answer': '"81.2%"'},
 {'Question': '"What is the American Tower Corp\'s current ratio in 12 years ago?"',
  'Answer': 1.7923},
 {'Question': '"What is the DISH Network Corporation\'s current ratio in 13 years ago?"',
  'Answer': 1.7804},
 {'Question': '"What is the American Tower Corp\'s current ratio in 2012?"',
  'Answer': 1.7923},
 {'Question': '"What is the DISH Network Corporation\'s current ratio in 2011?"',
  'Answer': 1.7804},
 {'Question': '"What is the International Paper Company\'s Operating Profit Margin in 2006?"',
  'Answer': 9.769119769},
 {'Question': '"What is the International Paper Company\'s Operating Profit Margin in 2005?"',
  'Answer': 6.59693166},
 {'Question': '"What is the International Paper Company\'s Operating Profit Margin in 2004?"',
  'Answer': 7.119831815},
 {'Question': '"What is the Air Products and Chemicals\'s Operating Profit Margin in 2016?"',
  'Answer': 26.7735375},
 {'Question': '"What is the Air Products and Chemicals\'s Operating Profit Margin in 2015?"',
  'Answer': 21.88472888},
 {'Question': '"What is the Air Products and Chemicals\'s Operating Profit Margin in 2014?"',
  'Answer': 18.69805075},
 {'Question': '"What is the difference of Operating Profit Margin between Air Products and Chemicals in 2016 and International Paper Company in 2006?"',
  'Answer': '17.00441774'},
 {'Question': '"What is the average of Operating Profit Margin between Air Products and Chemicals in 2016 and International Paper Company in 2005?"',
  'Answer': '16.68523458'},
 {'Question': '"What is the sum of Operating Profit Margin between Air Products and Chemicals in 2016 and International Paper Company in 2004?"',
  'Answer': '33.89336932'},
 {'Question': '"Which one\'s Operating Profit Margin is bigger between Air Products and Chemicals in 2014 and International Paper Company in 2006?"',
  'Answer': 'Air Products and Chemicals'},
 {'Question': '"What is the difference of Operating Profit Margin between Air Products and Chemicals in 2015 and International Paper Company in 2006?"',
  'Answer': '12.11560911'},
 {'Question': '"What is the average of Operating Profit Margin between Air Products and Chemicals in 2015 and International Paper Company in 2005?"',
  'Answer': '14.24083027'},
 {'Question': '"What is the sum of Operating Profit Margin between Air Products and Chemicals in 2015 and International Paper Company in 2004?"',
  'Answer': '29.00456069'},
 {'Question': '"Which one\'s current ratio is bigger between American Tower Corp in 2012 and DISH Network Corporation in 2011?"',
  'Answer': 'American Tower Corp'},
 {'Question': '"What is the average of current ratio between American Tower Corp in 2012 and DISH Network Corporation in 2011?"',
  'Answer': '1.786341177'},
 {'Question': '"What is the difference of current ratio between American Tower Corp in 2012 and DISH Network Corporation in a year before that?"',
  'Answer': '0.01185521735'},
 {'Question': '"What is the Goldman Sachs Group\'s Total Assets change from 2014 to 2016 multiplied by the average of current ratio between American Tower Corp in 2012 and DISH Network Corporation in 2011?"',
  'Answer': '48722.45 million'},
 {'Question': '"What is the Goldman Sachs Group\'s Total Assets change from 2013 to 2017 multiplied by the average of current ratio between American Tower Corp in 2012 and DISH Network Corporation in 2011?"',
  'Answer': '46296.6 million'},
 {'Question': '"What is the sum of Goldman Sachs Group\'s Total Assets from 2011 to 2014 divided by the average of Operating Profit Margin between Air Products and Chemicals in 2016 and International Paper Company in 2005?',
  'Answer': '217529.28 million'},
 {'Question': '"What is the sum of Goldman Sachs Group\'s Total Assets from 2011 to 2014 multiplied by the average of Operating Profit Margin between Air Products and Chemicals in 2015 and International Paper Company in 2005?"',
  'Answer': '51687477.96 million'},
 {'Question': '"What is the Goldman Sachs Group\'s Total Assets change from 2014 to 2016 divided the difference of Operating Profit Margin between Air Products and Chemicals in 2016 and International Paper Company in 2006?"',
  'Answer': '1604 million'},
 {'Question': '"What is the Goldman Sachs Group\'s Total Assets change from 2013 to 2017 dividied the sum of Operating Profit Margin between Air Products and Chemicals in 2016 and International Paper Company in 2004?"',
  'Answer': '764.6 million'},
 {'Question': '"What is the difference of Union Pacific Corp\'s revenue from 2013 to 2016 divided the sum of Operating Profit Margin between Air Products and Chemicals in 2015 and International Paper Company in 2004?"',
  'Answer': '-69.7 million'},
 {'Question': '"What is the average of Union Pacific Corp\'s revenue from 2013 to 2016 divided by the sum of Operating Profit Margin between Air Products and Chemicals in 2015 and International Paper Company in 2004?"',
  'Answer': '755.95 million'},
 {'Question': '"What is the difference of Union Pacific Corp\'s revenue from 2013 to 2016 multiplied by the average of current ratio between American Tower Corp in 2012 and DISH Network Corporation in 2011?"',
  'Answer': '-3611.98 million'},
 {'Question': '"What is the average of Union Pacific Corp\'s revenue from 2013 to 2016 divided by the average of Operating Profit Margin between Air Products and Chemicals in 2015 and International Paper Company in 2005?"',
  'Answer': '1539.67 million'}]

In [42]:
score_answer_prompt = PromptTemplate(
    input_variables=["question", "answer", "response"],
    template="""
    You have to score the response by comparing with the answer.
    You should score 0 or 1 as JSON with "score" key.
    You can ignore minor difference with the unit or numerical value.
    Question: {question}
    Answer: {answer}
    Response: {response}
    Score:

    Output JSON: {{
      "score": 1 if the answer response is meaningfully the same as the answer, 0 if the response is different from the answer>
    }}
    """
)

from pydantic import BaseModel, Field

class Score(BaseModel):
    """Score of the response"""
    score: int = Field(description="score of the response")

score_answer_chain = score_answer_prompt | llm.with_structured_output(Score)

In [43]:
score_answer_chain.invoke({'question': qa_dict[0]['Question'], 'answer': qa_dict[0]['Answer'], 'response': 'it is 375 B'}).score

1

### Accuracy score

In [44]:
import json

# Initialize variables
results = []
correct = 0

# JSON file name to save the results
output_file = "test_results.json"

# Iterate over all questions in the dataset
for i, item in enumerate(qa_dict):
    # Generate model's response
    response = agentic_rag(item['Question'])
    print(response)
    
    # Compute the score for the response
    score = score_answer_chain.invoke({
        'question': item['Question'],
        'answer': item['Answer'],
        'response': response
    }).score
    correct += score

    # Record the result for each question
    result = {
        "index": i,  
        "question": item['Question'],  
        "model_answer": response,  
        "correct_answer": item['Answer'],  
        "score": score  
    }
    results.append(result)

    print(i, correct)

# Calculate overall accuracy
accuracy = correct / len(qa_dict)
print(f"Accuracy: {correct}/{len(qa_dict)}")

# Save results to a JSON file
with open(output_file, "w", encoding="utf-8") as f:
    json.dump(results, f, ensure_ascii=False, indent=4)

print(f"Results saved to {output_file}")


It seems that there is no available data for the High-Quality Liquid Assets (HQLA) for Citigroup in Q4 of 2015. You may want to check Citigroup's financial reports or other financial databases for that specific information. If you have another question or need information on a different topic, feel free to ask!
0 0
It seems that there is no available data regarding the recorded net losses of American Tower in 2008 based on the financial reports. You may want to check other sources or rephrase your question for more specific information. If you have any other questions or need assistance with a different topic, feel free to ask!
1 0
It seems that there is no available data for the port call costs of Royal Caribbean Cruises (ticker: RCL) for the fiscal year 2012. You may want to check other financial metrics or specify a different question related to Royal Caribbean Cruises.
2 0
It seems that there is no available data for the aggregate rent expense of American Tower Corp in 2014. You ma

In [48]:
test_question = "what was the hqla in the q4 of Citigroup in 2015"
response = agentic_rag(test_question)
print("Generated Response:", response)


Generated Response: It seems that I couldn't retrieve the data for the High-Quality Liquid Assets (HQLA) for Citigroup in Q4 of 2015. This could be due to the specific nature of the data or its availability in the financial reports.

If you have any other questions or need information on a different topic, feel free to ask!


In [47]:
query = "what was the hqla in the q4 of Citigroup in 2015"
retrieved_docs = docsearch.similarity_search(query, k=5)

for idx, doc in enumerate(retrieved_docs):
    print(f"Document {idx+1}:", doc.page_content)


Document 1: note : amounts set forth in the table above are presented on an average basis .
as set forth in the table above , citi 2019s lcr increased both year-over-year and sequentially .
the increase year-over-year was driven by both an increase in hqla and a reduction in net outflows .
sequentially , the increase was driven by a slight reduction in net outflows , as hqla remained largely unchanged .
Document 2: among other things , the final rules require citi to disclose components of its average hqla , lcr and inflows and outflows each quarter .
in addition , the final rules require disclosure of citi 2019s calculation of the maturity mismatch add-on as well as other qualitative disclosures .
the effective date for these disclosures is april 1 , 2017 .
Document 3: the table below sets forth the components of citi 2019s lcr calculation and hqla in excess of net outflows for the periods indicated : in billions of dollars dec .
31 , sept .
30 , dec .
31 .
Document 4: the table below